# Conversational Analytics API

How it works:
- Create:
  - **Data Source Definition:** The soure BigQuery, Looker, or Looker Studio sources
  - **Context** for the using the data source
  - **Agent** that uses the context
  - **Conversation** that is a session with the agent
  - **Chat** message within the conversation


In [1]:
!gcloud services enable bigquery.googleapis.com
#!gcloud services enable cloudaicompanion.googleapis.com
!gcloud services enable geminidataanalytics.googleapis.com

In [2]:
import subprocess
from google.cloud import geminidataanalytics

In [3]:
# what project are we working in?
PROJECT_ID = subprocess.run(['gcloud', 'config', 'get-value', 'project'], capture_output=True, text=True, check=True).stdout.strip()
PROJECT_ID

'statmike-mlops-349915'

---
## Helper Functions

These are copied directly from the documentation [here](https://cloud.google.com/gemini/docs/conversational-analytics-api/build-agent-sdk#define_helper_functions).  The functions are used to parse and display the responses from the API.

In [4]:
import pandas as pd
import json as json_lib
import altair as alt
from IPython.display import display, HTML

import proto
from google.protobuf.json_format import MessageToDict, MessageToJson

def handle_text_response(resp):
  parts = getattr(resp, 'parts')
  print(''.join(parts))

def display_schema(data):
  fields = getattr(data, 'fields')
  df = pd.DataFrame({
    "Column": map(lambda field: getattr(field, 'name'), fields),
    "Type": map(lambda field: getattr(field, 'type'), fields),
    "Description": map(lambda field: getattr(field, 'description', '-'), fields),
    "Mode": map(lambda field: getattr(field, 'mode'), fields)
  })
  display(df)

def display_section_title(text):
  display(HTML('<h2>{}</h2>'.format(text)))

def format_looker_table_ref(table_ref):
 return 'lookmlModel: {}, explore: {}, lookerInstanceUri: {}'.format(table_ref.lookml_model, table_ref.explore, table_ref.looker_instance_uri)

def format_bq_table_ref(table_ref):
  return '{}.{}.{}'.format(table_ref.project_id, table_ref.dataset_id, table_ref.table_id)

def display_datasource(datasource):
  source_name = ''
  if 'studio_datasource_id' in datasource:
   source_name = getattr(datasource, 'studio_datasource_id')
  elif 'looker_explore_reference' in datasource:
   source_name = format_looker_table_ref(getattr(datasource, 'looker_explore_reference'))
  else:
    source_name = format_bq_table_ref(getattr(datasource, 'bigquery_table_reference'))

  print(source_name)
  display_schema(datasource.schema)

def handle_schema_response(resp):
  if 'query' in resp:
    print(resp.query.question)
  elif 'result' in resp:
    display_section_title('Schema resolved')
    print('Data sources:')
    for datasource in resp.result.datasources:
      display_datasource(datasource)

def handle_data_response(resp):
  if 'query' in resp:
    query = resp.query
    display_section_title('Retrieval query')
    print('Query name: {}'.format(query.name))
    print('Question: {}'.format(query.question))
    print('Data sources:')
    for datasource in query.datasources:
      display_datasource(datasource)
  elif 'generated_sql' in resp:
    display_section_title('SQL generated')
    print(resp.generated_sql)
  elif 'result' in resp:
    display_section_title('Data retrieved')

    fields = [field.name for field in resp.result.schema.fields]
    d = {}
    for el in resp.result.data:
      for field in fields:
        if field in d:
          d[field].append(el[field])
        else:
          d[field] = [el[field]]

    display(pd.DataFrame(d))

def handle_chart_response(resp):
  def _value_to_dict(v):
    if isinstance(v, proto.marshal.collections.maps.MapComposite):
      return _map_to_dict(v)
    elif isinstance(v, proto.marshal.collections.RepeatedComposite):
      return [_value_to_dict(el) for el in v]
    elif isinstance(v, (int, float, str, bool)):
      return v
    else:
      return MessageToDict(v)

  def _map_to_dict(d):
    out = {}
    for k in d:
      if isinstance(d[k], proto.marshal.collections.maps.MapComposite):
        out[k] = _map_to_dict(d[k])
      else:
        out[k] = _value_to_dict(d[k])
    return out

  if 'query' in resp:
    print(resp.query.instructions)
  elif 'result' in resp:
    vegaConfig = resp.result.vega_config
    vegaConfig_dict = _map_to_dict(vegaConfig)
    alt.Chart.from_json(json_lib.dumps(vegaConfig_dict)).display();

def show_message(msg):
  m = msg.system_message
  if 'text' in m:
    handle_text_response(getattr(m, 'text'))
  elif 'schema' in m:
    handle_schema_response(getattr(m, 'schema'))
  elif 'data' in m:
    handle_data_response(getattr(m, 'data'))
  elif 'chart' in m:
    handle_chart_response(getattr(m, 'chart'))
  print('\n')

---
## Data Source Definition

In [5]:
datasource = geminidataanalytics.DatasourceReferences(
    bq = dict(
        table_references = [
            geminidataanalytics.BigQueryTableReference(
                project_id='bigquery-public-data', 
                dataset_id='noaa_tsunami', 
                table_id='historical_runups'
            ),
            geminidataanalytics.BigQueryTableReference(
                project_id='bigquery-public-data', 
                dataset_id='noaa_tsunami', 
                table_id='historical_source_event'
            ),
            geminidataanalytics.BigQueryTableReference(
                project_id='bigquery-public-data', 
                dataset_id='noaa_significant_earthquakes', 
                table_id='earthquakes'
            )   
        ]
    )
)

---
## Context

- **Stateful:** The API manages the conversation
  - Used Here
- **Stateless:** The client manages the conversation and must supply the full history on each turn
  - Check out [this example](https://cloud.google.com/gemini/docs/conversational-analytics-api/build-agent-sdk#create-a-stateless-multi-turn-conversation) in the documentation.

In [6]:
context = geminidataanalytics.Context(
    system_instruction = 'Help users explore, analyze, and give details reports for earthquakes and tsunamis.',
    datasource_references = datasource,
    options = dict(
        #chart = dict(image = dict(svg = )),
        analysis = dict(python = dict(enabled = True))
    )
)

---
## Agent

In [7]:
agent_id = 'agent_1'

agent_client = geminidataanalytics.DataAgentServiceClient()
agent_response = agent_client.create_data_agent(
    parent = f"projects/{PROJECT_ID}/locations/global",
    data_agent_id = agent_id,
    data_agent = dict(
        data_analytics_agent = dict(published_context = context)
    )
)

---
## Conversation

In [10]:
conversation_id = 'conversation_001'

conversation_client = geminidataanalytics.DataChatServiceClient()
conversation_response = conversation_client.create_conversation(
    parent = f"projects/{PROJECT_ID}/locations/global",
    conversation_id = conversation_id,
    conversation = dict(
        agents = [f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}"],
        name = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}" 
    )
)

---
## Chat - Stateful

In [16]:
questions = [
    'How many earthquakes happen per year on average?',
    'How many tsunamis happen per year on average?',
    'Are there more earthquakes or tsunamis per year on average?',
    'Plot the timeseries for earthquakes and tsunami count by year.'
]

### Question 1

In [12]:
stream = conversation_client.chat(
    request = dict(
        parent = f"projects/{PROJECT_ID}/locations/global",
        messages = [
            dict(user_message = dict(text = questions[0]))
        ],
        conversation_reference = dict(
            conversation = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}",
            data_agent_context = dict(data_agent = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
        )
    )
)

for response in stream:
    show_message(response)

How many earthquakes happen per year on average?




Data sources:
bigquery-public-data.noaa_tsunami.historical_runups


Column      Type  \
0                             id     INT64   
1                     tsevent_id     INT64   
2                           year     INT64   
3                          month     INT64   
4                            day     INT64   
5                      timestamp  DATETIME   
6                       doubtful    STRING   
7                        country    STRING   
8                          state    STRING   
9                  location_name    STRING   
10                      latitude     FLOAT   
11                     longitude     FLOAT   
12                   region_code     INT64   
13          distance_from_source     INT64   
14                       arr_day     INT64   
15                      arr_hour     INT64   
16                       arr_min     INT64   
17             travel_time_hours     INT64   
18           travel_time_minutes     INT64   
19                      water_ht     FLOAT   
20         horizontal_inundation     FLOAT   
21           type_measurement_id     INT64   
22                        period     FLOAT   
23                  first_motion    STRING   
24                        deaths     INT64   
25            deaths_description     INT64   
26                      injuries     INT64   
27          injuries_description     INT64   
28       damage_millions_dollars     FLOAT   
29            damage_description     INT64   
30                houses_damaged     INT64   
31    houses_damaged_description     INT64   
32              houses_destroyed     INT64   
33  houses_destroyed_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   The unique numeric identifier of the tsunami s...  NULLABLE  
2   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
3   Valid values: 1-12 The Date and Time are given...  NULLABLE  
4   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
5                                   Timestamp in UTC.  NULLABLE  
6   A "?" in the Doubtful column indicates a doubt...  NULLABLE  
7   The country where the tsunami effects were obs...  NULLABLE  
8   The State, Province or Prefecture where the ts...  NULLABLE  
9   The location (city, state or island) where the...  NULLABLE  
10  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
11  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
12  Regional boundaries are based on frequency of ...  NULLABLE  
13  The distance from the tsunami event source to ...  NULLABLE  
14                                                     NULLABLE  
15                                                     NULLABLE  
16                                                     NULLABLE  
17                                                     NULLABLE  
18                                                     NULLABLE  
19  The maximum water height above sea level in me...  NULLABLE  
20  The maximum horizontal distance of inland floo...  NULLABLE  
21  Valid values: 1, 2, 3, 4, 5, 6, 7, 8, 9, 10  S...  NULLABLE  
22  The period is in minutes and, when available, ...  NULLABLE  
23  The first motion of the wave whether rise or f...  NULLABLE  
24  Deaths from the tsunami at the specific runup ...  NULLABLE  
25  Valid values: 0 to 4 When a description was fo...  NULLABLE  
26  Whenever possible, numbers of injuries from th...  NULLABLE  
27  Valid values: 0 to 4 When a description was fo...  NULLABLE  
28  The value in the Damage column should be multi...  NULLABLE  
29  For those events not offering a monetary evalu...  NULLABLE  
30  Valid values: 0 to Whenever possible, number o...  NULLABLE  
31  Valid values: 0 to 4 For those events not offe...  NULLABLE  
32  Whenever possible, number of houses destroyed ...  NULLABLE  
33  Valid values: 0 to 4 For those events not offe...  NULLABLE

bigquery-public-data.noaa_tsunami.historical_source_event


Column      Type  \
0                                   id     INT64   
1                                 year     INT64   
2                                month     INT64   
3                                  day     INT64   
4                            timestamp  DATETIME   
5                       event_validity     INT64   
6                           cause_code     INT64   
7                          focal_depth     INT64   
8                    primary_magnitude     FLOAT   
9                              country    STRING   
10                               state    STRING   
11                       location_name    STRING   
12                            latitude     FLOAT   
13                           longitude     FLOAT   
14                         region_code     INT64   
15                maximum_water_height     FLOAT   
16                                 abe     FLOAT   
17                                iida     FLOAT   
18                            soloviev     FLOAT   
19                      warning_status     INT64   
20                              deaths     INT64   
21                  deaths_description     INT64   
22                             missing     INT64   
23                 missing_description     INT64   
24                            injuries     INT64   
25                injuries_description     INT64   
26             damage_millions_dollars     FLOAT   
27                  damage_description     INT64   
28                    houses_destroyed     INT64   
29        houses_destroyed_description     INT64   
30                      houses_damaged     INT64   
31          houses_damaged_description     INT64   
32                        total_deaths     INT64   
33            total_deaths_description     INT64   
34                       total_missing     INT64   
35           total_missing_description     INT64   
36                      total_injuries     INT64   
37          total_injuries_description     INT64   
38    total_damage_in_millions_dollars     FLOAT   
39            total_damage_description     INT64   
40              total_houses_destroyed     INT64   
41  total_houses_destroyed_description     INT64   
42                total_houses_damaged     INT64   
43    total_houses_damaged_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
2   Valid values: 1-12 The Date and Time are given...  NULLABLE  
3   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
4                                   Timestamp in UTC.  NULLABLE  
5   Valid values: -1 to 4 Validity of the actual t...  NULLABLE  
6   Valid values: 0 to 11 The source of the tsunam...  NULLABLE  
7   Valid values: 0 to 700 km The depth of the ear...  NULLABLE  
8   Valid values: 0.0 to 9.9 The value in this col...  NULLABLE  
9   The Country where the tsunami source occurred ...  NULLABLE  
10  The two-letter State or Province abbreviation ...  NULLABLE  
11  The Country, State, Province or Island where t...  NULLABLE  
12  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
13  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
14  Regional boundaries are based on frequency of ...  NULLABLE  
15  The maximum water height above sea level in me...  NULLABLE  
16  Valid values: -5 to 10 Abe defined two differe...  NULLABLE  
17  Valid values: -5 to 10 Tsunami magnitude (M) i...  NULLABLE  
18  Valid values: -5 to 10 Tsunami intensity is de...  NULLABLE  
19  Valid values: -1 to 4 Warning Status of the Ts...  NULLABLE  
20  If an actual number of deaths due to the tsuna...  NULLABLE  
21  Valid values: 0 to 4 When a description was fo...  NULLABLE  
22  Whenever possible, numbers of Missing from the...  NULLABLE  
23  Valid values: 0 to 4 When a description was fo...  NULLABLE  
24  Whenever possible, numbers of injurie

...

bigquery-public-data.noaa_tsunami.historical_runups


Column      Type  \
0                             id     INT64   
1                     tsevent_id     INT64   
2                           year     INT64   
3                          month     INT64   
4                            day     INT64   
5                      timestamp  DATETIME   
6                       doubtful    STRING   
7                        country    STRING   
8                          state    STRING   
9                  location_name    STRING   
10                      latitude     FLOAT   
11                     longitude     FLOAT   
12                   region_code     INT64   
13          distance_from_source     INT64   
14                       arr_day     INT64   
15                      arr_hour     INT64   
16                       arr_min     INT64   
17             travel_time_hours     INT64   
18           travel_time_minutes     INT64   
19                      water_ht     FLOAT   
20         horizontal_inundation     FLOAT   
21           type_measurement_id     INT64   
22                        period     FLOAT   
23                  first_motion    STRING   
24                        deaths     INT64   
25            deaths_description     INT64   
26                      injuries     INT64   
27          injuries_description     INT64   
28       damage_millions_dollars     FLOAT   
29            damage_description     INT64   
30                houses_damaged     INT64   
31    houses_damaged_description     INT64   
32              houses_destroyed     INT64   
33  houses_destroyed_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   The unique numeric identifier of the tsunami s...  NULLABLE  
2   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
3   Valid values: 1-12 The Date and Time are given...  NULLABLE  
4   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
5                                   Timestamp in UTC.  NULLABLE  
6   A "?" in the Doubtful column indicates a doubt...  NULLABLE  
7   The country where the tsunami effects were obs...  NULLABLE  
8   The State, Province or Prefecture where the ts...  NULLABLE  
9   The location (city, state or island) where the...  NULLABLE  
10  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
11  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
12  Regional boundaries are based on frequency of ...  NULLABLE  
13  The distance from the tsunami event source to ...  NULLABLE  
14                                                     NULLABLE  
15                                                     NULLABLE  
16                                                     NULLABLE  
17                                                     NULLABLE  
18                                                     NULLABLE  
19  The maximum water height above sea level in me...  NULLABLE  
20  The maximum horizontal distance of inland floo...  NULLABLE  
21  Valid values: 1, 2, 3, 4, 5, 6, 7, 8, 9, 10  S...  NULLABLE  
22  The period is in minutes and, when available, ...  NULLABLE  
23  The first motion of the wave whether rise or f...  NULLABLE  
24  Deaths from the tsunami at the specific runup ...  NULLABLE  
25  Valid values: 0 to 4 When a description was fo...  NULLABLE  
26  Whenever possible, numbers of injuries from th...  NULLABLE  
27  Valid values: 0 to 4 When a description was fo...  NULLABLE  
28  The value in the Damage column should be multi...  NULLABLE  
29  For those events not offering a monetary evalu...  NULLABLE  
30  Valid values: 0 to Whenever possible, number o...  NULLABLE  
31  Valid values: 0 to 4 For those events not offe...  NULLABLE  
32  Whenever possible, number of houses destroyed ...  NULLABLE  
33  Valid values: 0 to 4 For those events not offe...  NULLABLE

SELECT year, COUNT(id) AS count_of_earthquakes
FROM `bigquery-public-data`.`noaa_significant_earthquakes`.`earthquakes`
GROUP BY year
ORDER BY year;






year count_of_earthquakes
0    -2150                    1
1    -2000                    2
2    -1610                    1
3    -1566                    1
4    -1450                    1
..     ...                  ...
948   2017                   64
949   2018                   66
950   2019                   62
951   2020                   29
952   2021                   30

[953 rows x 2 columns]













The average number of earthquakes per year is 6.58.




### Question 2

In [13]:
stream = conversation_client.chat(
    request = dict(
        parent = f"projects/{PROJECT_ID}/locations/global",
        messages = [
            dict(user_message = dict(text = questions[1]))
        ],
        conversation_reference = dict(
            conversation = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}",
            data_agent_context = dict(data_agent = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
        )
    )
)

for response in stream:
    show_message(response)

How many tsunamis happen per year on average?




Data sources:
bigquery-public-data.noaa_tsunami.historical_runups


Column      Type  \
0                             id     INT64   
1                     tsevent_id     INT64   
2                           year     INT64   
3                          month     INT64   
4                            day     INT64   
5                      timestamp  DATETIME   
6                       doubtful    STRING   
7                        country    STRING   
8                          state    STRING   
9                  location_name    STRING   
10                      latitude     FLOAT   
11                     longitude     FLOAT   
12                   region_code     INT64   
13          distance_from_source     INT64   
14                       arr_day     INT64   
15                      arr_hour     INT64   
16                       arr_min     INT64   
17             travel_time_hours     INT64   
18           travel_time_minutes     INT64   
19                      water_ht     FLOAT   
20         horizontal_inundation     FLOAT   
21           type_measurement_id     INT64   
22                        period     FLOAT   
23                  first_motion    STRING   
24                        deaths     INT64   
25            deaths_description     INT64   
26                      injuries     INT64   
27          injuries_description     INT64   
28       damage_millions_dollars     FLOAT   
29            damage_description     INT64   
30                houses_damaged     INT64   
31    houses_damaged_description     INT64   
32              houses_destroyed     INT64   
33  houses_destroyed_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   The unique numeric identifier of the tsunami s...  NULLABLE  
2   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
3   Valid values: 1-12 The Date and Time are given...  NULLABLE  
4   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
5                                   Timestamp in UTC.  NULLABLE  
6   A "?" in the Doubtful column indicates a doubt...  NULLABLE  
7   The country where the tsunami effects were obs...  NULLABLE  
8   The State, Province or Prefecture where the ts...  NULLABLE  
9   The location (city, state or island) where the...  NULLABLE  
10  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
11  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
12  Regional boundaries are based on frequency of ...  NULLABLE  
13  The distance from the tsunami event source to ...  NULLABLE  
14                                                     NULLABLE  
15                                                     NULLABLE  
16                                                     NULLABLE  
17                                                     NULLABLE  
18                                                     NULLABLE  
19  The maximum water height above sea level in me...  NULLABLE  
20  The maximum horizontal distance of inland floo...  NULLABLE  
21  Valid values: 1, 2, 3, 4, 5, 6, 7, 8, 9, 10  S...  NULLABLE  
22  The period is in minutes and, when available, ...  NULLABLE  
23  The first motion of the wave whether rise or f...  NULLABLE  
24  Deaths from the tsunami at the specific runup ...  NULLABLE  
25  Valid values: 0 to 4 When a description was fo...  NULLABLE  
26  Whenever possible, numbers of injuries from th...  NULLABLE  
27  Valid values: 0 to 4 When a description was fo...  NULLABLE  
28  The value in the Damage column should be multi...  NULLABLE  
29  For those events not offering a monetary evalu...  NULLABLE  
30  Valid values: 0 to Whenever possible, number o...  NULLABLE  
31  Valid values: 0 to 4 For those events not offe...  NULLABLE  
32  Whenever possible, number of houses destroyed ...  NULLABLE  
33  Valid values: 0 to 4 For those events not offe...  NULLABLE

bigquery-public-data.noaa_tsunami.historical_source_event


Column      Type  \
0                                   id     INT64   
1                                 year     INT64   
2                                month     INT64   
3                                  day     INT64   
4                            timestamp  DATETIME   
5                       event_validity     INT64   
6                           cause_code     INT64   
7                          focal_depth     INT64   
8                    primary_magnitude     FLOAT   
9                              country    STRING   
10                               state    STRING   
11                       location_name    STRING   
12                            latitude     FLOAT   
13                           longitude     FLOAT   
14                         region_code     INT64   
15                maximum_water_height     FLOAT   
16                                 abe     FLOAT   
17                                iida     FLOAT   
18                            soloviev     FLOAT   
19                      warning_status     INT64   
20                              deaths     INT64   
21                  deaths_description     INT64   
22                             missing     INT64   
23                 missing_description     INT64   
24                            injuries     INT64   
25                injuries_description     INT64   
26             damage_millions_dollars     FLOAT   
27                  damage_description     INT64   
28                    houses_destroyed     INT64   
29        houses_destroyed_description     INT64   
30                      houses_damaged     INT64   
31          houses_damaged_description     INT64   
32                        total_deaths     INT64   
33            total_deaths_description     INT64   
34                       total_missing     INT64   
35           total_missing_description     INT64   
36                      total_injuries     INT64   
37          total_injuries_description     INT64   
38    total_damage_in_millions_dollars     FLOAT   
39            total_damage_description     INT64   
40              total_houses_destroyed     INT64   
41  total_houses_destroyed_description     INT64   
42                total_houses_damaged     INT64   
43    total_houses_damaged_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
2   Valid values: 1-12 The Date and Time are given...  NULLABLE  
3   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
4                                   Timestamp in UTC.  NULLABLE  
5   Valid values: -1 to 4 Validity of the actual t...  NULLABLE  
6   Valid values: 0 to 11 The source of the tsunam...  NULLABLE  
7   Valid values: 0 to 700 km The depth of the ear...  NULLABLE  
8   Valid values: 0.0 to 9.9 The value in this col...  NULLABLE  
9   The Country where the tsunami source occurred ...  NULLABLE  
10  The two-letter State or Province abbreviation ...  NULLABLE  
11  The Country, State, Province or Island where t...  NULLABLE  
12  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
13  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
14  Regional boundaries are based on frequency of ...  NULLABLE  
15  The maximum water height above sea level in me...  NULLABLE  
16  Valid values: -5 to 10 Abe defined two differe...  NULLABLE  
17  Valid values: -5 to 10 Tsunami magnitude (M) i...  NULLABLE  
18  Valid values: -5 to 10 Tsunami intensity is de...  NULLABLE  
19  Valid values: -1 to 4 Warning Status of the Ts...  NULLABLE  
20  If an actual number of deaths due to the tsuna...  NULLABLE  
21  Valid values: 0 to 4 When a description was fo...  NULLABLE  
22  Whenever possible, numbers of Missing from the...  NULLABLE  
23  Valid values: 0 to 4 When a description was fo...  NULLABLE  
24  Whenever possible, numbers of injurie

...

bigquery-public-data.noaa_tsunami.historical_runups


Column      Type  \
0                             id     INT64   
1                     tsevent_id     INT64   
2                           year     INT64   
3                          month     INT64   
4                            day     INT64   
5                      timestamp  DATETIME   
6                       doubtful    STRING   
7                        country    STRING   
8                          state    STRING   
9                  location_name    STRING   
10                      latitude     FLOAT   
11                     longitude     FLOAT   
12                   region_code     INT64   
13          distance_from_source     INT64   
14                       arr_day     INT64   
15                      arr_hour     INT64   
16                       arr_min     INT64   
17             travel_time_hours     INT64   
18           travel_time_minutes     INT64   
19                      water_ht     FLOAT   
20         horizontal_inundation     FLOAT   
21           type_measurement_id     INT64   
22                        period     FLOAT   
23                  first_motion    STRING   
24                        deaths     INT64   
25            deaths_description     INT64   
26                      injuries     INT64   
27          injuries_description     INT64   
28       damage_millions_dollars     FLOAT   
29            damage_description     INT64   
30                houses_damaged     INT64   
31    houses_damaged_description     INT64   
32              houses_destroyed     INT64   
33  houses_destroyed_description     INT64   

                                          Description      Mode  
0        The unique numeric identifier of the record.  NULLABLE  
1   The unique numeric identifier of the tsunami s...  NULLABLE  
2   Valid values: -2000 to Present Format +/-yyyy ...  NULLABLE  
3   Valid values: 1-12 The Date and Time are given...  NULLABLE  
4   Valid values: 1-31 (where months apply) The Da...  NULLABLE  
5                                   Timestamp in UTC.  NULLABLE  
6   A "?" in the Doubtful column indicates a doubt...  NULLABLE  
7   The country where the tsunami effects were obs...  NULLABLE  
8   The State, Province or Prefecture where the ts...  NULLABLE  
9   The location (city, state or island) where the...  NULLABLE  
10  Valid values: -90 to +90 Latitude: 0 to 90 (No...  NULLABLE  
11  Valid values: -180 to +180 Longitude: 0 to 180...  NULLABLE  
12  Regional boundaries are based on frequency of ...  NULLABLE  
13  The distance from the tsunami event source to ...  NULLABLE  
14                                                     NULLABLE  
15                                                     NULLABLE  
16                                                     NULLABLE  
17                                                     NULLABLE  
18                                                     NULLABLE  
19  The maximum water height above sea level in me...  NULLABLE  
20  The maximum horizontal distance of inland floo...  NULLABLE  
21  Valid values: 1, 2, 3, 4, 5, 6, 7, 8, 9, 10  S...  NULLABLE  
22  The period is in minutes and, when available, ...  NULLABLE  
23  The first motion of the wave whether rise or f...  NULLABLE  
24  Deaths from the tsunami at the specific runup ...  NULLABLE  
25  Valid values: 0 to 4 When a description was fo...  NULLABLE  
26  Whenever possible, numbers of injuries from th...  NULLABLE  
27  Valid values: 0 to 4 When a description was fo...  NULLABLE  
28  The value in the Damage column should be multi...  NULLABLE  
29  For those events not offering a monetary evalu...  NULLABLE  
30  Valid values: 0 to Whenever possible, number o...  NULLABLE  
31  Valid values: 0 to 4 For those events not offe...  NULLABLE  
32  Whenever possible, number of houses destroyed ...  NULLABLE  
33  Valid values: 0 to 4 For those events not offe...  NULLABLE

SELECT t1.year, COUNT(t1.id) AS count_of_tsunamis
FROM `bigquery-public-data`.`noaa_tsunami`.`historical_source_event` AS t1
GROUP BY t1.year
ORDER BY t1.year;






year count_of_tsunamis
0     None                 1
1    -2000                 1
2    -1610                 1
3    -1365                 1
4    -1300                 1
..     ...               ...
562   2017                20
563   2018                19
564   2019                 8
565   2020                14
566   2021                12

[567 rows x 2 columns]



























The average number of tsunamis per year is 4.95.




### Question 3

In [15]:
stream = conversation_client.chat(
    request = dict(
        parent = f"projects/{PROJECT_ID}/locations/global",
        messages = [
            dict(user_message = dict(text = questions[2]))
        ],
        conversation_reference = dict(
            conversation = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}",
            data_agent_context = dict(data_agent = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
        )
    )
)

for response in stream:
    show_message(response)

On average, there are more earthquakes per year (6.58) than tsunamis per year (4.95).




### Question 4

In [17]:
stream = conversation_client.chat(
    request = dict(
        parent = f"projects/{PROJECT_ID}/locations/global",
        messages = [
            dict(user_message = dict(text = questions[3]))
        ],
        conversation_reference = dict(
            conversation = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}",
            data_agent_context = dict(data_agent = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
        )
    )
)

for response in stream:
    show_message(response)

Generate a line chart showing the count of earthquakes per year. The x-axis should be 'year' and the y-axis should be 'count_of_earthquakes'.




alt.Chart(...)



Generate a line chart showing the count of tsunamis per year. The x-axis should be 'year' and the y-axis should be 'count_of_tsunamis'.




alt.Chart(...)

ServiceUnavailable: 503 The service is currently unavailable. [detail: "[ORIGINAL ERROR] RPC::DEADLINE_EXCEEDED: Server deadline (119.997530765s) expired."
]

### Conversation History

In [18]:
history = conversation_client.list_messages(parent = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}")

In [19]:
history

ListMessagesPager<messages {
  message_id: "2a42a840-fb58-476d-bf9d-e4e154d00d98"
  message {
    timestamp {
      seconds: 1757211768
      nanos: 757000000
    }
    system_message {
      chart {
        result {
          vega_config {
            fields {
              key: "title"
              value {
                string_value: "Tsunami Count per Year"
              }
            }
            fields {
              key: "mark"
              value {
                struct_value {
                  fields {
                    key: "type"
                    value {
                      string_value: "line"
                    }
                  }
                  fields {
                    key: "tooltip"
                    value {
                      bool_value: true
                    }
                  }
                  fields {
                    key: "point"
                    value {
                      bool_value: true
                    }
            

In [23]:
for message in history:
    print(message)

message_id: "2a42a840-fb58-476d-bf9d-e4e154d00d98"
message {
  timestamp {
    seconds: 1757211768
    nanos: 757000000
  }
  system_message {
    chart {
      result {
        vega_config {
          fields {
            key: "title"
            value {
              string_value: "Tsunami Count per Year"
            }
          }
          fields {
            key: "mark"
            value {
              struct_value {
                fields {
                  key: "type"
                  value {
                    string_value: "line"
                  }
                }
                fields {
                  key: "tooltip"
                  value {
                    bool_value: true
                  }
                }
                fields {
                  key: "point"
                  value {
                    bool_value: true
                  }
                }
                fields {
                  key: "interpolate"
                  value {
         

---
## Cleanup

In [83]:
delete_agent = False
delete_convos = False

In [82]:
response = agent_client.get_data_agent(name = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
print(f"The agent is present: {response.name}")
if delete_agent:
    agent_client.delete_data_agent(name = f"projects/{PROJECT_ID}/locations/global/dataAgents/{agent_id}")
    print("The agent has been deleted.")
else:
    print("NOT deleting the agent.")

The agent is present: projects/statmike-mlops-349915/locations/global/dataAgents/convo_agent
The agent has been deleted.


In [9]:
conversation_client.get_conversation(name = f"projects/{PROJECT_ID}/locations/global/conversations/{conversation_id}")

name: "projects/statmike-mlops-349915/locations/global/conversations/conversation_1"
agents: "projects/statmike-mlops-349915/locations/global/dataAgents/convo_agent"
create_time {
  seconds: 1757209401
  nanos: 323197000
}
last_used_time {
  seconds: 1757210826
  nanos: 941000000
}